In [1]:
import numpy as np
import matplotlib.pyplot as plt

In [2]:
def rel_error(x, y):
  """ returns relative error """
  return np.max(np.abs(x - y) / (np.maximum(1e-8, np.abs(x) + np.abs(y))))

In [3]:
def eval_numerical_gradient_array(f, x, df, h=1e-5):
  """
  Evaluate a numeric gradient for a function that accepts a numpy
  array and returns a numpy array.
  """
  grad = np.zeros_like(x)
  it = np.nditer(x, flags=['multi_index'], op_flags=['readwrite'])
  while not it.finished:
    ix = it.multi_index
    
    oldval = x[ix]
    x[ix] = oldval + h
    pos = f(x)
    x[ix] = oldval - h
    neg = f(x)
    x[ix] = oldval
    
    grad[ix] = np.sum((pos - neg) * df) / (2 * h)
    it.iternext()
   
  return grad

In [4]:
def eval_numerical_gradient(f, x, verbose=False, h=0.00001):
  """ 
  a naive implementation of numerical gradient of f at x 
  - f should be a function that takes a single argument
  - x is the point (numpy array) to evaluate the gradient at
  """ 

  fx = f(x) # evaluate function value at original point
  grad = np.zeros_like(x)
  # iterate over all indexes in x
  it = np.nditer(x, flags=['multi_index'], op_flags=['readwrite'])
  while not it.finished:

    # evaluate function at x+h
    ix = it.multi_index
    oldval = x[ix]
    x[ix] = oldval + h # increment by h
    fxph = f(x) # evalute f(x + h)
    x[ix] = oldval - h
    fxmh = f(x) # evaluate f(x - h)
    x[ix] = oldval # restore

    # compute the partial derivative with centered formula
    grad[ix] = (fxph - fxmh) / (2 * h) # the slope
    if verbose:
      print ix, grad[ix]
    it.iternext() # step to next dimension

  return grad

In [5]:
def affine_forward(x, w, b):
  """
  Computes the forward pass for an affine (fully-connected) layer.

  The input x has shape (N, d_1, ..., d_k) where x[i] is the ith input.
  We multiply this against a weight matrix of shape (D, M) where
  D = \prod_i d_i

  Inputs:
  x - Input data, of shape (N, d_1, ..., d_k)
  w - Weights, of shape (D, M)
  b - Biases, of shape (M,)
  
  Returns a tuple of:
  - out: output, of shape (N, M)
  - cache: (x, w, b)
  """
  out = None
  #############################################################################
  # TODO: Implement the affine forward pass. Store the result in out. You     #
  # will need to reshape the input into rows.                                 #
  #############################################################################
  N = x.shape[0]
  D = np.prod(x.shape[1:])
  x2 = np.reshape(x, (N, D))
  out = np.dot(x2, w) + b
  #############################################################################
  #                             END OF YOUR CODE                              #
  #############################################################################
  cache = (x, w, b)
  return out, cache

In [6]:
def affine_backward(dout, cache):
  """
  Computes the backward pass for an affine layer.

  Inputs:
  - dout: Upstream derivative, of shape (N, M)
  - cache: Tuple of:
    - x: Input data, of shape (N, d_1, ... d_k)
    - w: Weights, of shape (D, M)

  Returns a tuple of:
  - dx: Gradient with respect to x, of shape (N, d1, ..., d_k)
  - dw: Gradient with respect to w, of shape (D, M)
  - db: Gradient with respect to b, of shape (M,)
  """
  x, w, b = cache
  dx, dw, db = None, None, None
  #############################################################################
  # TODO: Implement the affine backward pass.                                 #
  #############################################################################
  N = x.shape[0]
  D = x.shape[1]
 

  dx = np.dot(dout, w.T) # N x D
  dw = np.dot(x.T, dout) # D x M
  db = np.dot(dout.T, np.ones(N)) # M x 1


  #############################################################################
  #                             END OF YOUR CODE                              #
  #############################################################################
  return dx, dw, db

In [7]:
x = np.random.randn(1, 3)
w = np.random.randn(3, 2)
b = np.random.randn(2)
dout = np.random.randn(1, 2)

dx_num = eval_numerical_gradient_array(lambda x: affine_forward(x, w, b)[0], x, dout)
dw_num = eval_numerical_gradient_array(lambda w: affine_forward(x, w, b)[0], w, dout)
db_num = eval_numerical_gradient_array(lambda b: affine_forward(x, w, b)[0], b, dout)

_, cache = affine_forward(x, w, b)
dx, dw, db = affine_backward(dout, cache)

print dx_num, dx
# The error should be less than 1e-10
print 'Testing affine_backward function:'
print 'dx error: ', rel_error(dx_num, dx)
print 'dw error: ', rel_error(dw_num, dw)
print 'db error: ', rel_error(db_num, db)

[[ 0.65601626  1.54592553 -0.26321276]] [[ 0.65601626  1.54592553 -0.26321276]]
Testing affine_backward function:
dx error:  1.41939897976e-11
dw error:  8.06399577286e-12
db error:  7.82659241604e-12


In [8]:
def sigmoid_forward(z):
        sigmoidfn = 1.0 / (1.0 + np.exp(-z)) # sigmoid activation function
        return sigmoidfn
    
def sigmoid_backward(dout,fw_activation):
        return np.multiply(np.multiply(fw_activation,1-fw_activation),dout)

In [9]:
x = np.random.randn(1, 3)
w = np.random.randn(3, 2)
b = np.random.randn(2)
dout = np.random.randn(1, 2)

dx_num = eval_numerical_gradient_array(lambda x: sigmoid_forward(affine_forward(x, w, b)[0]), x, dout)
dw_num = eval_numerical_gradient_array(lambda w: sigmoid_forward(affine_forward(x, w, b)[0]), w, dout)
db_num = eval_numerical_gradient_array(lambda b: sigmoid_forward(affine_forward(x, w, b)[0]), b, dout)

y, cache = affine_forward(x, w, b)
sigout = sigmoid_forward(y)
douty = sigmoid_backward(dout,sigout)
dx, dw, db = affine_backward(douty, cache)

print dx_num, dx
# The error should be less than 1e-10
print 'Testing affine_backward function:'
print 'dx error: ', rel_error(dx_num, dx)
print 'dw error: ', rel_error(dw_num, dw)
print 'db error: ', rel_error(db_num, db)

[[-0.22941518 -0.19002241 -0.31639747]] [[-0.22941518 -0.19002241 -0.31639747]]
Testing affine_backward function:
dx error:  6.96144585938e-12
dw error:  2.9325838647e-11
db error:  3.39523198143e-12


In [10]:
def euclidean_sq_loss(z,t):
    #z is lower layer's activation, t is the target value
    m = z.shape[0] #number of training sample in a batch
    n = z.shape[1] #size of feature

    loss = 0.5* np.dot( z[0,:]-t[0,:],np.transpose(z[0,:]-t[0,:]) )
    dout = (z - t)
    
    return loss,dout

In [11]:
def piano_fw(x,w,b,t):
    loss,_ = euclidean_sq_loss(sigmoid_forward(affine_forward(x, w, b)[0]),t)
    return loss

In [12]:
x = np.random.randn(1, 3)
w = np.random.randn(3, 2)
b = np.random.randn(2)
t = np.array([[0,1]])

y, cache = affine_forward(x, w, b)
sigout = sigmoid_forward(y)
loss,dout = euclidean_sq_loss(sigout,t)
print loss, 0.5* (np.linalg.norm(sigout-t))**2

dw_num = eval_numerical_gradient(lambda w: piano_fw(x,w,b,t), w)
db_num = eval_numerical_gradient(lambda b: piano_fw(x,w,b,t), b)

print 'dw_num:',dw_num,'db_num:',db_num

douty = sigmoid_backward(dout,sigout)
dx, dw, db = affine_backward(douty, cache)
print dw,db
#print dx_num, dx
# The error should be less than 1e-10
#print 'Testing affine_backward function:'
#print 'dx error: ', rel_error(dx_num, dx)
print 'dw error: ', rel_error(dw_num, dw)
print 'db error: ', rel_error(db_num, db)

0.429564832765 0.429564832765
dw_num: [[-0.03007124  0.03301009]
 [ 0.09537521 -0.10469619]
 [ 0.03673193 -0.04032173]] db_num: [ 0.11668635 -0.12809006]
[[-0.03007124  0.03301009]
 [ 0.09537521 -0.10469619]
 [ 0.03673193 -0.04032173]] [ 0.11668635 -0.12809006]
dw error:  3.22966611489e-11
db error:  7.87184044273e-12


In [13]:
class NeuralNet_Piano:
    #class variables
    # num_classes  is the size of the last affine activation
    # input_dim   is the size of input dimension
    # num_hidden_layers is how many hidden layers
    ## (constructor ) Dict model
    ## (constructor) num_layers is how many totol layers = hidden_layers + 2(Softmax cross entropy loss layer)
    ## (Forward) Dict input cache
    ## (Backward) Dict gradient cache 
    #class def
    # constructor to construct the neural network, given the hyper parameter
    # Forward
    # Backward
    # applyGrad
    def __init__(self,model_hyper):
        num_classes = model_hyper['num_classes']
        input_dim  = model_hyper['input_dim']
        self.num_hidden_layers = model_hyper['num_hidden_layers']
        self.num_layers = self.num_hidden_layers + 1
        layer_list = [None] * self.num_hidden_layers
        cur_layer_size = input_dim
        self.learnrate = model_hyper['learnrate']
        self.NN_model = []
        self.NN_grad = []
        self.NN_num_grad = []
        for hid_layer_iter in range(self.num_hidden_layers):  
            layer_model = {}
            next_layer_size = model_hyper['layer_sizes'][hid_layer_iter]
            layer_model['W'] = 0.9 * np.random.randn(cur_layer_size, next_layer_size)
            layer_model['b'] =0.9 * np.random.randn(next_layer_size)
            self.NN_model.append(layer_model)
            cur_layer_size = next_layer_size
        
        layer_model = {}   
        next_layer_size = num_classes
        layer_model['W'] = 0.9 * np.random.randn(cur_layer_size, next_layer_size)
        self.NN_model.append(layer_model)
        self.NN_cache=[]
        self.sigmoid_on = False
        for i in self.NN_model:
            print i['W'].shape
            if 'b' in i:
                print i['b'].shape
            print "__________________"
            
    def affine_backward(self,dout, cache):
        x = cache['x']
        w = cache['w']
        b = cache['b']
        #print x,w,b
        grad_cache = {}
        dx, dw, db = None, None, None
        N = x.shape[0]
        D = np.prod(x.shape[1:])
        x2 = np.reshape(x, (N, D))

        dx2 = np.dot(dout, w.T) # N x D
        dw = np.dot(x2.T, dout) # D x M
        db = np.dot(dout.T, np.ones(N)) # M x 1

        dx = np.reshape(dx2, x.shape)
        grad_cache['dx'] = dx
        grad_cache['dw'] = dw
        #print grad_cache['dw']
        grad_cache['db'] = db
        return grad_cache
    
    def affine_backward2(self,dout, cache):
        x = cache['x']
        w = cache['w']

        grad_cache = {}
        dx, dw = None, None
        N = x.shape[0]
        D = np.prod(x.shape[1:])
        x2 = np.reshape(x, (N, D))

        dx2 = np.dot(dout, w.T) # N x D
        dw = np.dot(x2.T, dout) # D x M       

        dx = np.reshape(dx2, x.shape)
        grad_cache['dx'] = dx
        grad_cache['dw'] = dw
 
        return grad_cache  

    def affine_forward(self,x, w, b): 
        cache = {}
        out = None
        N = x.shape[0]
        D = np.prod(x.shape[1:])
        x2 = np.reshape(x, (N, D))
        out = np.dot(x2, w) + b
        cache['x'] = x
        cache['w'] = w
        cache['b'] = b
        return out, cache    
    
    def affine_forward2(self,x, w): 
        out = None
        cache = {}
        N = x.shape[0]
        D = np.prod(x.shape[1:])
        x2 = np.reshape(x, (N, D))
        out = np.dot(x2, w) 
        cache['x'] = x
        cache['w'] = w
        return out, cache  

    def sigmoid_forward(self,z):
        sigmoidfn = 1.0 / (1.0 + np.exp(-z)) # sigmoid activation function
        return sigmoidfn
    
    def sigmoid_backward(self,dout,fw_activation):
        return np.multiply(np.multiply(fw_activation,1-fw_activation),dout)

    def euclidean_sq_loss(self,z,t):
        #z is lower layer's activation, t is the target value
        m = z.shape[0] #number of training sample in a batch
        n = z.shape[1] #size of feature
        #print z.shape, t.shape
        loss = 0.5* np.dot( z[0,:]-t[0,:],np.transpose(z[0,:]-t[0,:]) )
        dout = (z - t)
    
        return loss,dout
    
    def forward_train(self,x,y):
        activation = x
        #print activation

        for i in self.NN_model:
            if 'b' in i:
                activation, cache = self.affine_forward(activation, i['W'], i['b'])
                self.NN_cache.append(cache)
            else:
                activation, cache = self.affine_forward2(activation, i['W'])
                self.NN_cache.append(cache)
        

        if (self.sigmoid_on == True):
            sigout = self.sigmoid_forward(activation) 
            self.NN_cache.append(sigout)
            loss,dz = self.euclidean_sq_loss(sigout,y)
        else:
            loss,dz = self.euclidean_sq_loss(activation,y)
        #for i in self.NN_cache:
        #    print i['w'].shape,i['x'].shape
        #    if 'b' in i:
        #        print i['b'].shape
        #    print "__________________"   
        return loss,dz
    
    def forward_test(self,x):
        activation = x
        #print activation

        for i in self.NN_model:
            if 'b' in i:
                activation, cache = self.affine_forward(activation, i['W'], i['b'])
                self.NN_cache.append(cache)
            else:
                activation, cache = self.affine_forward2(activation, i['W'])
                self.NN_cache.append(cache)
 
        return self.sigmoid_forward(activation)
    
    def backward_train(self,dz):
        if self.sigmoid_on == True:
            sigactivation = self.NN_cache[-1]
            backgrad = sigmoid_backward(dz,sigactivation)
            for i in reversed(self.NN_cache[:-1]):
                if 'b' in i:
                    grad_cache = self.affine_backward(backgrad,i)
                else:
                    grad_cache = self.affine_backward2(backgrad,i)
                backgrad = grad_cache['dx']
                
                self.NN_grad.insert(0,grad_cache)
        else:
            backgrad = dz
            for i in reversed(self.NN_cache):
                if 'b' in i:
                    grad_cache = self.affine_backward(backgrad,i)
                else:
                    grad_cache = self.affine_backward2(backgrad,i)
                backgrad = grad_cache['dx']
                
                self.NN_grad.insert(0,grad_cache)     

           
    def Apply_UpdateW(self):
        for i in range(self.num_layers):
            delta_W = -self.learnrate * self.NN_grad[i]['dw'] 
            #print delta_W
            self.NN_model[i]['W'] += delta_W
            #print 'Apply Update',i
            if 'db' in self.NN_grad[i] :
                delta_b = -self.learnrate * self.NN_grad[i]['db'] 
                self.NN_model[i]['b'] += delta_b
        self.reset_cache()

    def reset_cache(self):
        del(self.NN_cache[:])
        del(self.NN_grad[:]) 
        del(self.NN_num_grad[:]) 
        
    def get_grad(self):
        return self.NN_grad

    def get_W(self):
        return self.NN_model
    def cal_num_grad(self,w,h,x,y):
        grad = np.zeros_like(w)
        #print "w.shape",w.shape
        # iterate over all indexes in w
        it = np.nditer(w, flags=['multi_index'], op_flags=['readwrite'])
        
        while not it.finished:
            
            # evaluate function at x+h
            ix = it.multi_index
            oldval = w[ix]
            w[ix] = oldval + h # increment by h
            fxph,_ = self.forward_train(x,y) # evalute f(x + h)
            w[ix] = oldval - h
            fxmh,_ = self.forward_train(x,y) # evaluate f(x - h)
            w[ix] = oldval # restore
            # compute the partial derivative with centered formula
            grad[ix] = (fxph - fxmh) / (2 * h) # the slope
            it.iternext()           
        return grad
    def get_numerical_gradient(self):
        return self.NN_num_grad
    def set_numerical_gradient(self,x,y, h=0.0001):        
        for i in self.NN_model:
            num_grad_cache = {}
            num_grad_cache['dw'] = self.cal_num_grad(i['W'],h,x,y)
            
            if 'b' in i:
                num_grad_cache['db'] = self.cal_num_grad(i['b'],h,x,y)
               
            self.NN_num_grad.append(num_grad_cache)
            
        return self.NN_num_grad
    
    def check_grad_numgrad(self,x,y, h=0.0001,verbose = True):       
        self.set_numerical_gradient(x,y, h)  
        if verbose:
            for i in range(self.num_hidden_layers+1):
                print i,"th layer"
                if (rel_error(self.NN_grad[i]['dw'],self.NN_num_grad[i]['dw'])<1e-7):
                    print 'grad W correct',rel_error(self.NN_grad[i]['dw'],self.NN_num_grad[i]['dw'])
                else:
                    print self.NN_grad[i]['dw'].flatten()
                    print self.NN_num_grad[i]['dw'].flatten()
                    print rel_error(self.NN_grad[i]['dw'],self.NN_num_grad[i]['dw'])
                    print np.linalg.norm(self.NN_grad[i]['dw'].flatten() - self.NN_num_grad[i]['dw'].flatten())**2
                    print '==========='
                if 'db' in self.NN_grad[i] :
                    if (rel_error(self.NN_grad[i]['db'],self.NN_num_grad[i]['db'])<1e-7):
                        print 'grad b correct',rel_error(self.NN_grad[i]['db'],self.NN_num_grad[i]['db'])
                    else:
                        print self.NN_grad[i]['db'].flatten()
                        print self.NN_num_grad[i]['db'].flatten()
                        print rel_error(self.NN_grad[i]['db'],self.NN_num_grad[i]['db'])
                        print '==========='

In [14]:
model_hyper = {}
model_hyper['num_classes'] = 4
model_hyper['input_dim']=4
model_hyper['num_hidden_layers']=0
model_hyper['learnrate']=0.0001
layer_size = [None] * model_hyper['num_hidden_layers']
#layer_size[0] = 4
#layer_size[1] = 4
#layer_size[2] = 5
#layer_size[3] = 6
model_hyper['layer_sizes'] = layer_size  

In [15]:
a_nn = NeuralNet_Piano(model_hyper)
w_org = a_nn.get_W()
w_org0 = w_org[0]['W'].copy()
num_inputs = 1
x = np.random.randn(num_inputs, model_hyper['input_dim'])
y = np.random.randint(model_hyper['num_classes'] , size=num_inputs)
y_onehot=np.zeros([num_inputs,model_hyper['num_classes']])
y_onehot[np.arange(num_inputs), y] = 1
y = y_onehot.astype(int)
print 'xshape',x.shape,y.shape
print y,'\n',y_onehot
print '----------'
loss,dz = a_nn.forward_train(x,y)
print 'dz shape',dz.shape
a_nn.backward_train(dz)
grad = a_nn.get_grad()
a_nn.check_grad_numgrad(x,y)
print y.dtype,x.dtype

(4, 4)
__________________
xshape (1, 4) (1, 4)
[[0 1 0 0]] 
[[ 0.  1.  0.  0.]]
----------
dz shape (1, 4)
0 th layer
grad W correct 2.73199938854e-11
int64 float64


In [16]:
w_after = a_nn.get_W()
print w_org[0]['W'] - w_after[0]['W']
grad_w = a_nn.get_grad()
delta_w = -model_hyper['learnrate'] * grad_w [0]['dw'] 
print delta_w

[[ 0.  0.  0.  0.]
 [ 0.  0.  0.  0.]
 [ 0.  0.  0.  0.]
 [ 0.  0.  0.  0.]]
[[ -3.43102697e-05   6.30926693e-05   1.17494530e-04   7.52578035e-05]
 [  8.09515715e-05  -1.48860699e-04  -2.77216323e-04  -1.77563088e-04]
 [ -5.18452578e-06   9.53375107e-06   1.77542591e-05   1.13719894e-05]
 [ -5.61736131e-05   1.03296862e-04   1.92364919e-04   1.23213917e-04]]


In [17]:
num_grad = a_nn.get_numerical_gradient()

In [18]:
for i in a_nn.get_W():
    print i['W'].shape
for i in grad:
    print i['dw'].shape
for i in num_grad:
    print i['dw'].shape

(4, 4)
(4, 4)
(4, 4)


In [19]:
print '=====num grad ====='
for i in range(model_hyper['num_hidden_layers']+1):
    print i,"th layer:W error",rel_error(grad[i]['dw'],num_grad[i]['dw'])    
    if 'db' in grad[i] :
        print i,"th layer:b error",rel_error(grad[i]['db'],num_grad[i]['db'])
    print "__________________"  

print grad[0]['dw'].flatten()
print num_grad[0]['dw'].flatten()
print "__________________"  


=====num grad =====
0 th layer:W error 2.73199938854e-11
__________________
[ 0.3431027  -0.63092669 -1.1749453  -0.75257803 -0.80951571  1.48860699
  2.77216323  1.77563088  0.05184526 -0.09533751 -0.17754259 -0.11371989
  0.56173613 -1.03296862 -1.92364919 -1.23213917]
[ 0.3431027  -0.63092669 -1.1749453  -0.75257803 -0.80951571  1.48860699
  2.77216323  1.77563088  0.05184526 -0.09533751 -0.17754259 -0.11371989
  0.56173613 -1.03296862 -1.92364919 -1.23213917]
__________________


In [20]:
a_nn.Apply_UpdateW()
print y.dtype,x.dtype
loss,dz = a_nn.forward_train(x,y)
print 'dz shape',dz.shape
a_nn.backward_train(dz)
grad = a_nn.get_grad()
a_nn.check_grad_numgrad(x,y)
num_grad = a_nn.get_numerical_gradient()
print '=====num grad ====='
for i in range(model_hyper['num_hidden_layers']+1):
    print i,"th layer:W error",rel_error(grad[i]['dw'],num_grad[i]['dw'])    
    if 'db' in grad[i] :
        print i,"th layer:b error",rel_error(grad[i]['db'],num_grad[i]['db'])
    print "__________________"  

print grad[0]['dw'].flatten()
print num_grad[0]['dw'].flatten()
print "__________________"  


int64 float64
dz shape (1, 4)
0 th layer
grad W correct 2.0265418299e-11
=====num grad =====
0 th layer:W error 2.0265418299e-11
__________________
[ 0.34302021 -0.630775   -1.17466281 -0.7523971  -0.80932109  1.48824909
  2.77149673  1.77520398  0.05183279 -0.09531459 -0.17749991 -0.11369255
  0.56160107 -1.03272027 -1.92318669 -1.23184293]
[ 0.34302021 -0.630775   -1.17466281 -0.7523971  -0.80932109  1.48824909
  2.77149673  1.77520398  0.05183279 -0.09531459 -0.17749991 -0.11369255
  0.56160107 -1.03272027 -1.92318669 -1.23184293]
__________________


In [21]:
w_after = a_nn.get_W()
w_after0= w_after[0]['W']
real_delta_w = w_org0 - w_after0

print 'w_after0:\n',w_after0
print 'w_org0:\n',w_org0
print 'real_delta_w:\n',real_delta_w
grad_w = a_nn.get_grad()
delta_w = model_hyper['learnrate'] * grad_w [0]['dw'] 
print 'delta_w:\n',delta_w

w_after0:
[[ 0.33477606  0.50038625 -1.48873666 -0.5696672 ]
 [-0.44718404  0.80686113  1.63047687  0.1672542 ]
 [ 0.66656748 -0.37275812 -0.54456121 -0.70596669]
 [-0.10261548  0.60539328  0.54288921 -1.11777402]]
w_org0:
[[ 0.33481037  0.50032316 -1.48885415 -0.56974246]
 [-0.44726499  0.80700999  1.63075409  0.16743176]
 [ 0.66657267 -0.37276765 -0.54457896 -0.70597806]
 [-0.10255931  0.60528998  0.54269685 -1.11789723]]
real_delta_w:
[[  3.43102697e-05  -6.30926693e-05  -1.17494530e-04  -7.52578035e-05]
 [ -8.09515715e-05   1.48860699e-04   2.77216323e-04   1.77563088e-04]
 [  5.18452578e-06  -9.53375107e-06  -1.77542591e-05  -1.13719894e-05]
 [  5.61736131e-05  -1.03296862e-04  -1.92364919e-04  -1.23213917e-04]]
delta_w:
[[  3.43020206e-05  -6.30775002e-05  -1.17466281e-04  -7.52397095e-05]
 [ -8.09321086e-05   1.48824909e-04   2.77149673e-04   1.77520398e-04]
 [  5.18327928e-06  -9.53145890e-06  -1.77499905e-05  -1.13692552e-05]
 [  5.61601075e-05  -1.03272027e-04  -1.92318669e-0

In [22]:
w_org0 = w_after0.copy()
a_nn.Apply_UpdateW()
print y.dtype,x.dtype
loss,dz = a_nn.forward_train(x,y)
print 'dz shape',dz.shape
a_nn.backward_train(dz)
grad = a_nn.get_grad()
a_nn.check_grad_numgrad(x,y_onehot)
num_grad = a_nn.get_numerical_gradient()
print '=====num grad ====='
for i in range(model_hyper['num_hidden_layers']+1):
    print i,"th layer:W error",rel_error(grad[i]['dw'],num_grad[i]['dw'])    
    if 'db' in grad[i] :
        print i,"th layer:b error",rel_error(grad[i]['db'],num_grad[i]['db'])
    print "__________________"  

print grad[0]['dw'].flatten()
print num_grad[0]['dw'].flatten()
print "__________________"  


int64 float64
dz shape (1, 4)
0 th layer
grad W correct 1.83118276232e-11
=====num grad =====
0 th layer:W error 1.83118276232e-11
__________________
[ 0.34293774 -0.63062335 -1.17438039 -0.7522162  -0.8091265   1.48789127
  2.77083039  1.77477717  0.05182033 -0.09529167 -0.17745723 -0.11366522
  0.56146605 -1.03247197 -1.92272431 -1.23154677]
[ 0.34293774 -0.63062335 -1.17438039 -0.7522162  -0.8091265   1.48789127
  2.77083039  1.77477717  0.05182033 -0.09529167 -0.17745723 -0.11366522
  0.56146605 -1.03247197 -1.92272431 -1.23154677]
__________________


In [ ]:
w_after = a_nn.get_W()
w_after0= w_after[0]['W']
real_delta_w = w_org0 - w_after0

print 'w_after0:\n',w_after0
print 'w_org0:\n',w_org0
print 'real_delta_w:\n',real_delta_w
grad_w = a_nn.get_grad()
delta_w = model_hyper['learnrate'] * grad_w [0]['dw'] 
print 'delta_w:\n',delta_w

w_after0:
[[ 0.33474176  0.50044933 -1.48861919 -0.56959196]
 [-0.44710311  0.8067123   1.63019972  0.16707668]
 [ 0.6665623  -0.37274859 -0.54454346 -0.70595532]
 [-0.10267164  0.60549655  0.54308153 -1.11765083]]
w_org0:
[[ 0.33477606  0.50038625 -1.48873666 -0.5696672 ]
 [-0.44718404  0.80686113  1.63047687  0.1672542 ]
 [ 0.66656748 -0.37275812 -0.54456121 -0.70596669]
 [-0.10261548  0.60539328  0.54288921 -1.11777402]]
real_delta_w:
[[  3.43020206e-05  -6.30775002e-05  -1.17466281e-04  -7.52397095e-05]
 [ -8.09321086e-05   1.48824909e-04   2.77149673e-04   1.77520398e-04]
 [  5.18327928e-06  -9.53145890e-06  -1.77499905e-05  -1.13692552e-05]
 [  5.61601075e-05  -1.03272027e-04  -1.92318669e-04  -1.23184293e-04]]
delta_w:
[[  3.42937735e-05  -6.30623347e-05  -1.17438039e-04  -7.52216199e-05]
 [ -8.09126504e-05   1.48789127e-04   2.77083039e-04   1.77477717e-04]
 [  5.18203309e-06  -9.52916729e-06  -1.77457230e-05  -1.13665218e-05]
 [  5.61466051e-05  -1.03247197e-04  -1.92272431e-0

In [ ]:
num_train = 50000
y = np.random.randint(model_hyper['num_classes'] , size=num_train)
y_onehot=np.zeros([num_train,model_hyper['num_classes']])

y_onehot[np.arange(num_train), y] = 1
x = sigmoid_forward(y_onehot)
y = sigmoid_forward(y_onehot)
model2_hyper = {}
model2_hyper['num_classes'] = 4
model2_hyper['input_dim']=4
model2_hyper['num_hidden_layers']=0
model2_hyper['learnrate']=0.0005
layer_size = [None] * model2_hyper['num_hidden_layers']
#layer_size[0] = 4
#layer_size[1] = 4
#layer_size[2] = 5
#layer_size[3] = 6
model2_hyper['layer_sizes'] = layer_size  

num_round = 20
batch_size =1
num_train_batch = num_train/batch_size
num_rec = num_train
cost_rec = np.zeros(num_rec*num_round,dtype=np.float)
a_nn2 = NeuralNet_Piano(model2_hyper)

for ii in range(num_round):
    for i in range(num_rec):
        th_batch = i%num_train_batch
        Xbatch = x[th_batch*batch_size:th_batch*batch_size+batch_size,:]
        Ybatch = y[th_batch*batch_size:th_batch*batch_size+batch_size].astype(int)  
        #print Xbatch
        loss,dz = a_nn2.forward_train(Xbatch,Ybatch)
        print loss
        #if i < num_rec:
        cost_rec[ii*num_train+i] = loss
        a_nn2.backward_train(dz)
        #iris_nn.check_grad_numgrad(Xbatch,Ybatch,0.0001,True)
        a_nn2.Apply_UpdateW()

(4, 4)
__________________
1.649053911
1.64693646939
1.64482174664
1.64270973928
1.30503200925
2.26259909316
2.25969383855
1.63443055774
1.15064972969
1.63093728786
1.14777960018
1.62745239949
1.29164590416
1.28998738665
1.14207104013
1.14060458186
1.13914000657
1.61804854703
1.61597091736
1.61389595545
1.13355057671
1.13209505901
1.27653502221
1.12923553624
1.60614932188
1.60408697123
1.2703682023
1.12366034375
1.12221752544
1.12077655977
1.11933744434
1.59504493965
1.5929968474
1.1151993537
1.25867648624
1.11238289118
1.11095455351
1.10952804987
2.19483628665
1.25095100977
2.19005429231
2.18724218771
1.24542529351
1.09994131461
2.18067986814
1.57083623074
1.56881922331
1.23746824995
1.2358792984
2.16961459096
2.16682873163
1.55941381203
1.22890879665
1.22733083573
1.22575490097
1.08245098682
1.22283689027
1.07971871961
1.07833232386
2.14885564158
1.21667021779
2.14418201458
1.21319605129
2.13951939061
2.13677217456
1.53591574724
1.20634787216
1.06464983436
1.20347764503
1.52971178438


0.280720096665
0.133466262149
0.280308415049
0.133243849127
0.137230684508
0.137054475616
0.136878492983
0.432558822282
0.432003401963
0.136436287473
0.132310494348
0.136169293018
0.1320489582
0.430793194275
0.13577108673
0.279143782149
0.278785351988
0.135705253145
0.131404276682
0.278433004223
0.278075486724
0.131138486847
0.428301194176
0.277349142083
0.427430652082
0.135254838478
0.130447724996
0.276681479875
0.426241683966
0.425694375069
0.425147768935
0.275370852947
0.13471964859
0.134546663954
0.275131535547
0.13443118666
0.423586202735
0.129114525762
0.134043519902
0.422727869828
0.274216252924
0.128627870508
0.128462707924
0.128297757414
0.273731460928
0.420993870128
0.273066012243
0.133533338071
0.42001572154
0.127586283851
0.419291121622
0.272106351764
0.271756957904
0.133147794355
0.271468209582
0.271119635118
0.417385116037
0.132975591575
0.270522204742
0.416417775002
0.41588308034
0.132623611591
0.126220560905
0.269578234453
0.41473852469
0.268924482859
0.132371577622
0.2

0.0564720290645
0.102918067877
0.161586756099
0.0563867237513
0.161392978739
0.161185744635
0.15431694601
0.160895254548
0.0564247617428
0.154104280945
0.160619520324
0.153823351178
0.160330397203
0.0565186218684
0.153612186822
0.056515145308
0.0564425779289
0.153553202873
0.15335603531
0.159920271299
0.103853528829
0.159764018301
0.153138036928
0.0565798928841
0.103885409004
0.159540824206
0.15307203167
0.152875481947
0.159172570115
0.104137093333
0.159017533288
0.104052791926
0.158862831416
0.158658846109
0.1040183728
0.0566119647551
0.0565392730565
0.158535372082
0.158331807243
0.152760370688
0.104073479325
0.103939845419
0.056512600383
0.158163008777
0.152839300774
0.103972637652
0.0564979396821
0.103812028617
0.0563983679137
0.153068498827
0.103795045036
0.153015221979
0.152818745202
0.103948339678
0.0564801095073
0.157883780832
0.152754493265
0.152558351272
0.0565624848603
0.104097237881
0.0564626036268
0.056390103713
0.0563176968916
0.103882229684
0.0562184066389
0.157699921207


0.102967515526
0.102835301715
0.117230864143
0.139352356336
0.117216347372
0.117065837574
0.1028741767
0.139404090498
0.102700824071
0.0578326065789
0.0577583475345
0.139328174947
0.117253252677
0.102689180861
0.139244078983
0.102516266421
0.139024344737
0.102343809724
0.0579988416971
0.117548576583
0.139013289468
0.138834791651
0.0580306102115
0.117631212163
0.138864756288
0.138686449193
0.1177521288
0.0580239684592
0.138716636486
0.0580217589926
0.13861084295
0.138432861888
0.102321343521
0.102189959417
0.102058744014
0.0582280763151
0.101973129576
0.0581987734575
0.101887688037
0.0581695711087
0.118168423996
0.0580561906844
0.0579816445503
0.138551985549
0.118075390559
0.0579410091278
0.138582262545
0.118021127498
0.138540151595
0.0579728512643
0.138434663951
0.0579708426903
0.057896406146
0.138401823285
0.118161391826
0.138359936638
0.0579284559015
0.138254787536
0.118242725505
0.118090897802
0.102261574919
0.10213026756
0.101999128804
0.138228029345
0.118286415513
0.138186348756
0

0.0618590938882
0.0830897762591
0.123222143319
0.0617848981927
0.0831077997995
0.0617567227275
0.0830522670098
0.133583259064
0.0617968196172
0.0617174703877
0.133548181327
0.0829911963831
0.13334836614
0.133177142279
0.12361319921
0.082901694583
0.133105999563
0.132935086908
0.0827392852975
0.082633045226
0.0621384288633
0.123884044181
0.0826515276302
0.0620633982501
0.13294567667
0.0825688024101
0.0621033125761
0.0825140342431
0.13278790176
0.124107934596
0.132745287308
0.082426168005
0.132547305037
0.0622847053347
0.0622047296432
0.0823953794023
0.124257291928
0.06212936139
0.0620495851655
0.0619699113764
0.0825167429693
0.0619416658131
0.132860414422
0.124112568678
0.0618840491827
0.132886051104
0.0618730477534
0.123988102927
0.061747225482
0.123782622924
0.0827803956139
0.0826741027553
0.0617244173288
0.0826193091724
0.0825132231543
0.133064285878
0.0618163268279
0.123952149771
0.0825042012311
0.0617420420564
0.0824497003571
0.0617142220862
0.123847149178
0.123688125204
0.06154269

...

0.00343543593766
0.00210034911039
0.00343035427824
0.00329850426178
0.00329426886951
0.00343245852772
0.00329329404758
0.00166980146302
0.0032877856778
0.00210537377502
0.00328547481363
0.00210458198298
0.00166795545881
0.00328189347432
0.00166454136993
0.00327640972428
0.00327220270216
0.00345167829768
0.00327125658773
0.00211170053188
0.00326897218249
0.00166058579421
0.00326351508454
0.00345813511601
0.00326258071093
0.00325839144573
0.0032542075597
0.00325002904591
0.00212123072122
0.00346601734701
0.00165722984607
0.00324978589446
0.00212114729011
0.00211842366446
0.00211570353603
0.00346452082599
0.00325463596769
0.00211420970056
0.00211149498301
0.00210878375125
0.00166295009289
0.00325497003375
0.00325079054092
0.00346954763172
0.00211064944335
0.00325179583079
0.00210986476803
0.00324954667852
0.00347020202723
0.00166225958273
0.00324737707513
0.00211173254954
0.00347009904943
0.00166210106633
0.00210974416314
0.00166139132082
0.00324781225961
0.00324364195761
0.00347505284318

0.00308822062267
0.00207556487649
0.00161922998596
0.00308498581562
0.00207618025118
0.00308293014115
0.0016161854129
0.00343631775077
0.00161583168484
0.00161375690171
0.00207881509843
0.00161306114535
0.00307938359015
0.00160982582593
0.00307426798605
0.00208271188965
0.00344366706625
0.00160969672482
0.00160762981918
0.00208205200669
0.00160694313679
0.00307382763484
0.00306988073505
0.00160256855172
0.00208594847382
0.00160188879845
0.00159983191846
0.00208602739459
0.00306630270848
0.00345684150066
0.00208450702171
0.00345165443481
0.00208108465789
0.00207841247403
0.00207574372134
0.0016069622054
0.00307517892271
0.00344988667422
0.00307440023583
0.00344862728502
0.00344419912966
0.00307679481079
0.00160657666058
0.00307168545551
0.00160335763188
0.0034495574714
0.00306975954756
0.00208378481276
0.00306772524273
0.00208301725953
0.0034499790937
0.00344554920257
0.00344112499958
0.00207811821142
0.00207544983658
0.00207278488802
0.00343450518096
0.00343009515887
0.00161619544012
0

0.00326383509492
0.00305222078952
0.00156067661759
0.00326445246138
0.00305023060556
0.00304631400516
0.00304240243381
0.00303849588505
0.00303459435243
0.00155460445906
0.00302954929554
0.00205157287755
0.00327982982178
0.00155450063485
0.00302941664023
0.00205137988234
0.00327972334918
0.00155439687234
0.00327722391763
0.0015541135498
0.00155211801486
0.00303007990632
0.00205314261442
0.00302800015529
0.00205231804586
0.00155049063234
0.00205101078019
0.00204837721222
0.00328153341834
0.00155286768033
0.0020463787782
0.00303216103102
0.00328142377151
0.00204486659864
0.00327651549248
0.00155580601857
0.00204287769729
0.00327332841853
0.0030400066966
0.00155569455351
0.0020427044769
0.00155502661798
0.00155302991063
0.0030344565376
0.0020445534646
0.0030323722428
0.00155006997382
0.00204507165744
0.00328314733102
0.00327893165758
0.00303532216646
0.00327780970323
0.00204217195922
0.00203954974059
0.00203693088898
0.00327153196585
0.00155909237079
0.00155709044288
0.0015550910855
0.002

0.00192587871112
0.00297533486663
0.00151053495153
0.00192654309718
0.00150993397721
0.00150799517035
0.0029699394606
0.00296612595678
0.00327048558851
0.00192966712554
0.00296709233781
0.00192899056721
0.00296508438755
0.00327087421328
0.00192763516576
0.00326599559924
0.00326180194921
0.00192381032995
0.00297380169694
0.00325991723106
0.00297295822513
0.00192426832868
0.00151418723748
0.00151224296929
0.00296868749252
0.00296487559626
0.00296106859461
0.00150693949963
0.00193121445039
0.001928734705
0.00192625814369
0.00192378476236
0.00326913425753
0.00151198669178
0.00296521610542
0.0032695408421
0.00192310213187
0.00326466678582
0.00326047484204
0.00325628828085
0.00191862114495
0.00297690424181
0.00325441566894
0.00151863219545
0.00151668221978
0.00325350846442
0.00151637134213
0.00297563073011
0.00325394256003
0.00297478473002
0.00297096500471
0.00296715018405
0.00151154748105
0.0029622179949
0.0029584144057
0.00295461570044
0.00193389675364
0.00295262512551
0.00193321750957
0.0

0.00281472955472
0.00322987443403
0.00322572716481
0.00143984370925
0.00143799490069
0.00322475318003
0.00322061248668
0.00321647711012
0.00282359699766
0.00193128532098
0.00144115602153
0.00193009174267
0.00192761343888
0.00321470039349
0.00321057260825
0.00283002194991
0.00282638810495
0.00321226925408
0.00320814459052
0.00144614701964
0.00192709599984
0.0014455753238
0.00320649677662
0.00192520052567
0.00144659475121
0.00283186103632
0.00192576745526
0.00144497877932
0.0019245811872
0.00192210995915
0.00320564518304
0.00191893934521
0.00320082885799
0.0019157775834
0.0028417623555
0.00319893068953
0.00284102105379
0.00283737308561
0.00191788035824
0.00319994028362
0.00191472089207
0.00284014506737
0.00191401606941
0.00145427363877
0.00191284563339
0.00145369397643
0.00145182738365
0.00320141637877
0.00319730565067
0.00191157594266
0.00190912141378
0.0019066700366
0.00319113224246
0.00190353674903
0.00190109254275
0.00318567122177
0.00318158071099
0.001897297432
0.00146564589093
0.00

In [ ]:
Wmodel = a_nn2.get_W()
print Wmodel[0]['W']
print len(Wmodel)

#print Wmodel[0]['b']
#print len(Wmodel)

#print Wmodel[1]['W']
#print len(Wmodel)



In [ ]:
import matplotlib.pyplot as plt
plt.plot(cost_rec[0::100])
plt.show()


DataXy_ = np.loadtxt(open("iris_prep.txt", "rb"), delimiter=",", skiprows=1)
print DataXy_.shape
rand_idx = np.random.permutation(149)
DataXy =  DataXy_[rand_idx,:]
print DataXy[0:4,:]
num_train = 100
num_test = 49
trainX = DataXy[0:num_train,:-1]
meanX = trainX.mean()
#print trainX
trainX = 0.1*(trainX-meanX) 
trainY = DataXy[0:num_train,-1]
trainY_onehot = np.zeros([num_train,3])
trainY_onehot[np.arange(num_train), trainY.astype(int)] = 1
trainY = trainY_onehot
testX = 0.1*(DataXy[num_train:,:-1]-meanX) 
testY = DataXy[num_train:,-1]
testY_onehot = np.zeros([num_test,3])
testY_onehot[np.arange(num_test), testY.astype(int)] = 1
testY = testY_onehot
#print trainX

model_hyper2 = {}
model_hyper2['num_classes'] = 3
model_hyper2['input_dim']=4
model_hyper2['num_hidden_layers']=3
model_hyper2['learnrate']=0.0001
layer_size = [None] * model_hyper2['num_hidden_layers']
layer_size[0] = 5
layer_size[1] = 4
layer_size[2] = 5
#layer_size[3] = 6
model_hyper2['layer_sizes'] = layer_size    

batch_size =1
num_train_batch = num_train/batch_size
num_rec = num_train
cost_rec = np.zeros(num_rec,dtype=np.float)
iris_nn = NeuralNet_Piano(model_hyper2)
#iris_nn.reset_cache()
for i in range(50000):
    th_batch = i%num_train_batch
    Xbatch = trainX[th_batch*batch_size:th_batch*batch_size+batch_size,:]
    #print Xbatch
    Ybatch = trainY[th_batch*batch_size:th_batch*batch_size+batch_size].astype(int)  
    #print Ybatch
    loss_iris,dz_iris = iris_nn.forward_train(Xbatch,Ybatch)
    if i < num_rec:
        cost_rec[i] = loss_iris
    print loss_iris
    iris_nn.backward_train(dz_iris)
    #iris_nn.check_grad_numgrad(Xbatch,Ybatch,0.0001,True)
    iris_nn.Apply_UpdateW()

import matplotlib.pyplot as plt
plt.plot(cost_rec[0:100])
plt.show()